### 1. Xception Model

In [ ]:
from tensorflow.keras.applications import Xception
from tensorflow.keras.applications.xception import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#=======================load the cifar100 dataset=========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
testY = testY.flatten()

#=======================randomly select the 20 classes out of 100 classes===============================#
selected_classes = random.sample(range(100), 20)
class_map = {}
for new_index, original_class in enumerate(selected_classes):
    class_map[original_class] = new_index

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)
testX_resized = tf.image.resize(testX, (299, 299)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#===============load the Xception pretrained model======================================#
base_model = Xception(include_top=False, weights='imagenet', input_shape=(299, 299, 3))
base_model.trainable = False
x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=output, name="Xception-model")
model.summary(show_trainable = True)

#======================predict on test data================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#==============Evaluate accuracy=================#
acc = accuracy_score(testY, predY)*100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


Model: "Xception-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_11    │ (None, 299,     │         0 │ -              │   -   │
│ (InputLayer)      │ 299, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1      │ (None, 149,     │       864 │ input_layer_1… │   N   │
│ (Conv2D)          │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1_bn   │ (None, 149,     │       128 │ block1_conv1[… │   N   │
│ (BatchNormalizat… │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1_act  │ (None, 149,     │         0 │ block1_conv1_… │   -   │
│ (Activation)      │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2      │ (None, 147,     │    18,432 │ block1_conv1_… │   N   │
│ (Conv2D)          │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2_bn   │ (None, 147,     │       256 │ block1_conv2[… │   N   │
│ (BatchNormalizat… │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2_act  │ (None, 147,     │         0 │ block1_conv2_… │   -   │
│ (Activation)      │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv1   │ (None, 147,     │     8,768 │ block1_conv2_… │   N   │
│ (SeparableConv2D) │ 147, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv1_… │ (None, 147,     │       512 │ block2_sepcon… │   N   │
│ (BatchNormalizat… │ 147, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2_… │ (None, 147,     │         0 │ block2_sepcon… │   -   │
│ (Activation)      │ 147, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2   │ (None, 147,     │    17,536 │ block2_sepcon… │   N   │
│ (SeparableConv2D) │ 147, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2_… │ (None, 147,     │       512 │ block2_sepcon… │   N   │
│ (BatchNormalizat… │ 147, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_8 (Conv2D) │ (None, 74, 74,  │     8,192 │ block1_conv2_… │   N   │
│                   │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_pool       │ (None, 74, 74,  │         0 │ block2_sepcon… │   -   │
│ (MaxPooling2D)    │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 74, 74,  │       512 │ conv2d_8[0][0] │   N   │
│ (BatchNormalizat… │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ add_24 (Add)      │ (None, 74, 74,  │         0 │ block2_pool[0… │   -   │
│                   │ 128)            │           │ batch_normali… │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block3_sepconv1_… │ (None, 74, 74,  │         0 │ add_24[0][0]   │   - 

 Total params: 20,902,460 (79.74 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 20,861,480 (79.58 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 21s 283ms/step
Test accuracy on selected 20 classes: 7.65%


### 2. VGG16 Model

In [ ]:
from tensorflow.keras.applications import VGG16
from tensorflow.keras.applications.vgg16 import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#=======================load the cifar100 dataset=========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
testY = testY.flatten()

#=======================randomly select the 20 classes out of 100 classes===============================#
selected_classes = random.sample(range(100), 20)
class_map = {}
for new_index, original_class in enumerate(selected_classes):
    class_map[original_class] = new_index

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)
testX_resized = tf.image.resize(testX, (224,224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#===============load the vgg16 pretrained model======================================#
base_model = VGG16(include_top=False, weights='imagenet', input_shape=(224,224, 3))
base_model.trainable = False
x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=output, name="VGG16-model")
model.summary(show_trainable = True)

#======================predict on test data================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#==============Evaluate accuracy=================#
acc = accuracy_score(testY, predY)*100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")



Model: "VGG16-model"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_8 (InputLayer)  │ (None, 224, 224, 3)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv1 (Conv2D)       │ (None, 224, 224, 64)  │      1,792 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv2 (Conv2D)       │ (None, 224, 224, 64)  │     36,928 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_pool (MaxPooling2D)  │ (None, 112, 112, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv1 (Conv2D)       │ (None, 112, 112, 128) │     73,856 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv2 (Conv2D)       │ (None, 112, 112, 128) │    147,584 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_pool (MaxPooling2D)  │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv1 (Conv2D)       │ (None, 56, 56, 256)   │    295,168 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv2 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv3 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_pool (MaxPooling2D)  │ (None, 28, 28, 256)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv1 (Conv2D)       │ (None, 28, 28, 512)   │  1,180,160 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv2 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv3 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_pool (MaxPooling2D)  │ (None, 14, 14, 512)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv1 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv2 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv3 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_pool (MaxPooling2D)  │ (None, 7, 7, 512)     │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ global_average_pooling2d_8  │ (None, 512)           │          0 │   -   │
│ (GlobalAveragePooling2D)    │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ dense_8 (Dense)             │ (None, 20)            │     10,260 │   Y   │
└─────────────────────────────┴───────────────────────┴────────────┴───────┘

 Total params: 14,724,948 (56.17 MB)

 Trainable params: 10,260 (40.08 KB)

 Non-trainable params: 14,714,688 (56.13 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 11s 171ms/step
Test accuracy on selected 20 classes: 5.90%


### 3. VGG19 Model

In [ ]:
from tensorflow.keras.applications import VGG19
from tensorflow.keras.applications.vgg19 import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#=======================load the cifar100 dataset=========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
testY = testY.flatten()

#=======================randomly select the 20 classes out of 100 classes===============================#
selected_classes = random.sample(range(100), 20)
class_map = {}
for new_index, original_class in enumerate(selected_classes):
    class_map[original_class] = new_index

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)
testX_resized = tf.image.resize(testX, (224,224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#===============load the VGG19 pretrained model======================================#
base_model = VGG19(include_top=False, weights='imagenet', input_shape=(224, 224, 3))
base_model.trainable = False
x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=output, name="VGG19-model")
model.summary(show_trainable = True)

#======================predict on test data================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#==============Evaluate accuracy=================#
acc = accuracy_score(testY, predY)*100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


Model: "VGG19-model"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_17 (InputLayer) │ (None, 224, 224, 3)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv1 (Conv2D)       │ (None, 224, 224, 64)  │      1,792 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv2 (Conv2D)       │ (None, 224, 224, 64)  │     36,928 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_pool (MaxPooling2D)  │ (None, 112, 112, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv1 (Conv2D)       │ (None, 112, 112, 128) │     73,856 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv2 (Conv2D)       │ (None, 112, 112, 128) │    147,584 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_pool (MaxPooling2D)  │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv1 (Conv2D)       │ (None, 56, 56, 256)   │    295,168 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv2 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv3 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv4 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_pool (MaxPooling2D)  │ (None, 28, 28, 256)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv1 (Conv2D)       │ (None, 28, 28, 512)   │  1,180,160 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv2 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv3 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv4 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_pool (MaxPooling2D)  │ (None, 14, 14, 512)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv1 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv2 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv3 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv4 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_pool (MaxPooling2D)  │ (None, 7, 7, 512)     │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ global_average_pooling2d_17 │ (None, 512)           │          0 │   -   │
│ (GlobalAveragePooling2D)    │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ dense_17 (Dense)            │ (None, 20)            │     10,260 │   Y   │
└─────────────────────────────┴───────────────────────┴────────────┴─────

 Total params: 20,034,644 (76.43 MB)

 Trainable params: 10,260 (40.08 KB)

 Non-trainable params: 20,024,384 (76.39 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 14s 212ms/step
Test accuracy on selected 20 classes: 5.20%


### 4. ResNet50 Model

In [ ]:
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.applications.resnet50 import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#=======================load the cifar100 dataset=========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
testY = testY.flatten()

#=======================randomly select the 20 classes out of 100 classes===============================#
selected_classes = random.sample(range(100), 20)
class_map = {}
for new_index, original_class in enumerate(selected_classes):
    class_map[original_class] = new_index

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

testX_resized = tf.image.resize(testX, (224,224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#===============load the ResNet50 pretrained model======================================#
base_model = ResNet50(include_top=False, weights='imagenet', input_shape=(224, 224, 3))
base_model.trainable = False
x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=output, name="ResNet50-model")
model.summary(show_trainable = True)

#======================predict on test data================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#==============Evaluate accuracy=================#
acc = accuracy_score(testY, predY)*100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


Model: "ResNet50-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_19    │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_pad         │ (None, 230,     │         0 │ input_layer_1… │   -   │
│ (ZeroPadding2D)   │ 230, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_conv        │ (None, 112,     │     9,472 │ conv1_pad[0][… │   N   │
│ (Conv2D)          │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_bn          │ (None, 112,     │       256 │ conv1_conv[0]… │   N   │
│ (BatchNormalizat… │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_relu        │ (None, 112,     │         0 │ conv1_bn[0][0] │   -   │
│ (Activation)      │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ pool1_pad         │ (None, 114,     │         0 │ conv1_relu[0]… │   -   │
│ (ZeroPadding2D)   │ 114, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ pool1_pool        │ (None, 56, 56,  │         0 │ pool1_pad[0][… │   -   │
│ (MaxPooling2D)    │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_c… │ (None, 56, 56,  │     4,160 │ pool1_pool[0]… │   N   │
│ (Conv2D)          │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_bn │ (None, 56, 56,  │       256 │ conv2_block1_… │   N   │
│ (BatchNormalizat… │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_r… │ (None, 56, 56,  │         0 │ conv2_block1_… │   -   │
│ (Activation)      │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_2_c… │ (None, 56, 56,  │    36,928 │ conv2_block1_… │   N   │
│ (Conv2D)          │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_2_bn │ (None, 56, 56,  │       256 │ conv2_block1_… │   N   │
│ (BatchNormalizat… │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_2_r… │ (None, 56, 56,  │         0 │ conv2_block1_… │   -   │
│ (Activation)      │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_0_c… │ (None, 56, 56,  │    16,640 │ pool1_pool[0]… │   N   │
│ (Conv2D)          │ 256)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_3_c… │ (None, 56, 56,  │    16,640 │ conv2_block1_… │   N   │
│ (Conv2D)          │ 256)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_0_bn │ (None, 56, 56,  │     1,024 │ conv2_block1_… │   N   │
│ (BatchNormalizat… │ 256)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_3_bn │ (None, 56, 56,  │     1,024 │ conv2_block1_… │   N 

 Total params: 23,628,692 (90.14 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 23,587,712 (89.98 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 15s 175ms/step
Test accuracy on selected 20 classes: 5.70%


### 5. InceptionV3

In [ ]:
from tensorflow.keras.applications import InceptionV3
from tensorflow.keras.applications.inception_v3 import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#=======================load the cifar100 dataset=========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#=======================randomly select the 20 classes out of 100 classes===============================#
selected_classes = random.sample(range(100), 20)
class_map = {}
for new_index, original_class in enumerate(selected_classes):
    class_map[original_class] = new_index

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

testX_resized = tf.image.resize(testX, (299,299)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#===============load the InceptionV3 pretrained model======================================#
base_model = InceptionV3(include_top=False, weights='imagenet', input_shape=(299, 299, 3))
base_model.trainable = False
x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=output, name="InceptionV3-model")
model.summary(show_trainable = True)

#======================predict on test data================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#==============Evaluate accuracy=================#
acc = accuracy_score(testY, predY)*100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


169001437/169001437 ━━━━━━━━━━━━━━━━━━━━ 145s 1us/step
87910968/87910968 ━━━━━━━━━━━━━━━━━━━━ 5s 0us/step


Model: "InceptionV3-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer       │ (None, 299,     │         0 │ -              │   -   │
│ (InputLayer)      │ 299, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d (Conv2D)   │ (None, 149,     │       864 │ input_layer[0… │   N   │
│                   │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 149,     │        96 │ conv2d[0][0]   │   N   │
│ (BatchNormalizat… │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation        │ (None, 149,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 149, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_1 (Conv2D) │ (None, 147,     │     9,216 │ activation[0]… │   N   │
│                   │ 147, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 147,     │        96 │ conv2d_1[0][0] │   N   │
│ (BatchNormalizat… │ 147, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_1      │ (None, 147,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 147, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_2 (Conv2D) │ (None, 147,     │    18,432 │ activation_1[… │   N   │
│                   │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 147,     │       192 │ conv2d_2[0][0] │   N   │
│ (BatchNormalizat… │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_2      │ (None, 147,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 147, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ max_pooling2d     │ (None, 73, 73,  │         0 │ activation_2[… │   -   │
│ (MaxPooling2D)    │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_3 (Conv2D) │ (None, 73, 73,  │     5,120 │ max_pooling2d… │   N   │
│                   │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 73, 73,  │       240 │ conv2d_3[0][0] │   N   │
│ (BatchNormalizat… │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_3      │ (None, 73, 73,  │         0 │ batch_normali… │   -   │
│ (Activation)      │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_4 (Conv2D) │ (None, 71, 71,  │   138,240 │ activation_3[… │   N   │
│                   │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 71, 71,  │       576 │ conv2d_4[0][0] │   N   │
│ (BatchNormalizat… │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_4      │ (None, 71, 71,  │         0 │ batch_normali… │   - 

 Total params: 21,843,764 (83.33 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 21,802,784 (83.17 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 36s 350ms/step
Test accuracy on selected 20 classes: 5.70%


### 6. MobileNet Model

In [ ]:
from tensorflow.keras.applications import MobileNet
from tensorflow.keras.applications.mobilenet import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#======================= Load the CIFAR-100 dataset =========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#======================= Randomly select 20 classes out of 100 ==============================#
selected_classes = random.sample(range(100), 20)
class_map = {original: new for new, original in enumerate(selected_classes)}

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

#======================= Resize and preprocess test images ==================================#
testX_resized = tf.image.resize(testX, (224, 224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#======================= Load MobileNet pretrained model ====================================#
base_model = MobileNet(include_top=False, weights='imagenet', input_shape=(224, 224, 3))
base_model.trainable = False

x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=output, name="MobileNet-model")
model.summary(show_trainable=True)

#======================= Predict on test data ==============================================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#======================= Evaluate accuracy ==================================================#
acc = accuracy_score(testY, predY) * 100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


Model: "MobileNet-model"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_2 (InputLayer)  │ (None, 224, 224, 3)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1 (Conv2D)              │ (None, 112, 112, 32)  │        864 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1_bn                    │ (None, 112, 112, 32)  │        128 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1_relu (ReLU)           │ (None, 112, 112, 32)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1 (DepthwiseConv2D) │ (None, 112, 112, 32)  │        288 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1_bn                │ (None, 112, 112, 32)  │        128 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1_relu (ReLU)       │ (None, 112, 112, 32)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1 (Conv2D)          │ (None, 112, 112, 64)  │      2,048 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1_bn                │ (None, 112, 112, 64)  │        256 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1_relu (ReLU)       │ (None, 112, 112, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pad_2 (ZeroPadding2D)  │ (None, 113, 113, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2 (DepthwiseConv2D) │ (None, 56, 56, 64)    │        576 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2_bn                │ (None, 56, 56, 64)    │        256 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2_relu (ReLU)       │ (None, 56, 56, 64)    │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2 (Conv2D)          │ (None, 56, 56, 128)   │      8,192 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2_bn                │ (None, 56, 56, 128)   │        512 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2_relu (ReLU)       │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3 (DepthwiseConv2D) │ (None, 56, 56, 128)   │      1,152 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3_bn                │ (None, 56, 56, 128)   │        512 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3_relu (ReLU)       │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_3 (Conv2D)          │ (None, 56, 56, 128)   │     16,384 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_3_bn                │ (None, 56, 56, 128)   │        512 │   N 

 Total params: 3,249,364 (12.40 MB)

 Trainable params: 20,500 (80.08 KB)

 Non-trainable params: 3,228,864 (12.32 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 5s 53ms/step
Test accuracy on selected 20 classes: 5.05%


### 7. DenseNet121

In [ ]:
from tensorflow.keras.applications import MobileNet
from tensorflow.keras.applications.mobilenet import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#======================= Load the CIFAR-100 dataset =========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#======================= Randomly select 20 classes out of 100 ==============================#
selected_classes = random.sample(range(100), 20)
class_map = {original: new for new, original in enumerate(selected_classes)}

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

#======================= Resize and preprocess test images ==================================#
testX_resized = tf.image.resize(testX, (224, 224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#======================= Load MobileNet pretrained model ====================================#
base_model = MobileNet(include_top=False, weights='imagenet', input_shape=(224, 224, 3))
base_model.trainable = False

x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=output, name="MobileNet-model")
model.summary(show_trainable=True)

#======================= Predict on test data ==============================================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#======================= Evaluate accuracy ==================================================#
acc = accuracy_score(testY, predY) * 100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


Model: "MobileNet-model"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_3 (InputLayer)  │ (None, 224, 224, 3)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1 (Conv2D)              │ (None, 112, 112, 32)  │        864 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1_bn                    │ (None, 112, 112, 32)  │        128 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv1_relu (ReLU)           │ (None, 112, 112, 32)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1 (DepthwiseConv2D) │ (None, 112, 112, 32)  │        288 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1_bn                │ (None, 112, 112, 32)  │        128 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_1_relu (ReLU)       │ (None, 112, 112, 32)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1 (Conv2D)          │ (None, 112, 112, 64)  │      2,048 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1_bn                │ (None, 112, 112, 64)  │        256 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_1_relu (ReLU)       │ (None, 112, 112, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pad_2 (ZeroPadding2D)  │ (None, 113, 113, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2 (DepthwiseConv2D) │ (None, 56, 56, 64)    │        576 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2_bn                │ (None, 56, 56, 64)    │        256 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_2_relu (ReLU)       │ (None, 56, 56, 64)    │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2 (Conv2D)          │ (None, 56, 56, 128)   │      8,192 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2_bn                │ (None, 56, 56, 128)   │        512 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_2_relu (ReLU)       │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3 (DepthwiseConv2D) │ (None, 56, 56, 128)   │      1,152 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3_bn                │ (None, 56, 56, 128)   │        512 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_dw_3_relu (ReLU)       │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_3 (Conv2D)          │ (None, 56, 56, 128)   │     16,384 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ conv_pw_3_bn                │ (None, 56, 56, 128)   │        512 │   N 

 Total params: 3,249,364 (12.40 MB)

 Trainable params: 20,500 (80.08 KB)

 Non-trainable params: 3,228,864 (12.32 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 5s 53ms/step
Test accuracy on selected 20 classes: 6.25%


### 8. EfficientNetB1 Model

In [ ]:
from tensorflow.keras.applications import EfficientNetB1
from tensorflow.keras.applications.efficientnet import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#======================= Load the CIFAR-100 dataset =========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#======================= Randomly select 20 classes out of 100 ==============================#
selected_classes = random.sample(range(100), 20)
class_map = {original: new for new, original in enumerate(selected_classes)}

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

#======================= Resize and preprocess test images ==================================#
testX_resized = tf.image.resize(testX, (240, 240)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#======================= Load EfficientNetB1 pretrained model ===============================#
base_model = EfficientNetB1(include_top=False, weights='imagenet', input_shape=(240, 240, 3))
base_model.trainable = False

x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=output, name="EfficientNetB1-model")
model.summary(show_trainable=True)

#======================= Predict on test data ==============================================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#======================= Evaluate accuracy ==================================================#
acc = accuracy_score(testY, predY) * 100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


27018416/27018416 ━━━━━━━━━━━━━━━━━━━━ 1s 0us/step


Model: "EfficientNetB1-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_4     │ (None, 240,     │         0 │ -              │   -   │
│ (InputLayer)      │ 240, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ rescaling         │ (None, 240,     │         0 │ input_layer_4… │   -   │
│ (Rescaling)       │ 240, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ normalization     │ (None, 240,     │         7 │ rescaling[0][… │   N   │
│ (Normalization)   │ 240, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ rescaling_1       │ (None, 240,     │         0 │ normalization… │   -   │
│ (Rescaling)       │ 240, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv_pad     │ (None, 241,     │         0 │ rescaling_1[0… │   -   │
│ (ZeroPadding2D)   │ 241, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv         │ (None, 120,     │       864 │ stem_conv_pad… │   N   │
│ (Conv2D)          │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn           │ (None, 120,     │       128 │ stem_conv[0][… │   N   │
│ (BatchNormalizat… │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_activation   │ (None, 120,     │         0 │ stem_bn[0][0]  │   -   │
│ (Activation)      │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_dwconv    │ (None, 120,     │       288 │ stem_activati… │   N   │
│ (DepthwiseConv2D) │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_bn        │ (None, 120,     │       128 │ block1a_dwcon… │   N   │
│ (BatchNormalizat… │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_activati… │ (None, 120,     │         0 │ block1a_bn[0]… │   -   │
│ (Activation)      │ 120, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_squee… │ (None, 32)      │         0 │ block1a_activ… │   -   │
│ (GlobalAveragePo… │                 │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_resha… │ (None, 1, 1,    │         0 │ block1a_se_sq… │   -   │
│ (Reshape)         │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_reduce │ (None, 1, 1, 8) │       264 │ block1a_se_re… │   N   │
│ (Conv2D)          │                 │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_expand │ (None, 1, 1,    │       288 │ block1a_se_re… │   N   │
│ (Conv2D)          │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_excite │ (None, 120,     │         0 │ block1a_activ… │   -   │
│ (Multiply)        │ 120, 32)        │           │ block1a_se_ex… │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_project_… │ (None, 120,     │       512 │ block1a_se_ex… │   N 

 Total params: 6,600,859 (25.18 MB)

 Trainable params: 25,620 (100.08 KB)

 Non-trainable params: 6,575,239 (25.08 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 27s 217ms/step
Test accuracy on selected 20 classes: 6.65%


### 9. NASNetMobile

In [ ]:
from tensorflow.keras.applications import NASNetMobile
from tensorflow.keras.applications.nasnet import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#======================= Load the CIFAR-100 dataset =========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#======================= Randomly select 20 classes out of 100 ==============================#
selected_classes = random.sample(range(100), 20)
class_map = {original: new for new, original in enumerate(selected_classes)}

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

#======================= Resize and preprocess test images ==================================#
testX_resized = tf.image.resize(testX, (224, 224)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#======================= Load NASNetMobile pretrained model =================================#
base_model = NASNetMobile(include_top=False, weights='imagenet', input_shape=(224, 224, 3))
base_model.trainable = False

x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=output, name="NASNetMobile-model")
model.summary(show_trainable=True)

#======================= Predict on test data ==============================================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#======================= Evaluate accuracy ==================================================#
acc = accuracy_score(testY, predY) * 100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


19993432/19993432 ━━━━━━━━━━━━━━━━━━━━ 1s 0us/step


Model: "NASNetMobile-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_5     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv1        │ (None, 111,     │       864 │ input_layer_5… │   N   │
│ (Conv2D)          │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn1          │ (None, 111,     │       128 │ stem_conv1[0]… │   N   │
│ (BatchNormalizat… │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation        │ (None, 111,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_conv_1… │ (None, 111,     │       352 │ activation[0]… │   N   │
│ (Conv2D)          │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_bn_1_s… │ (None, 111,     │        44 │ reduction_con… │   N   │
│ (BatchNormalizat… │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_1      │ (None, 111,     │         0 │ reduction_bn_… │   -   │
│ (Activation)      │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_3      │ (None, 111,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 115,     │         0 │ activation_1[… │   -   │
│ (ZeroPadding2D)   │ 115, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 117,     │         0 │ activation_3[… │   -   │
│ (ZeroPadding2D)   │ 117, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │       396 │ separable_con… │   N   │
│ (SeparableConv2D) │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │     1,920 │ separable_con… │   N   │
│ (SeparableConv2D) │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │        44 │ separable_con… │   N   │
│ (BatchNormalizat… │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │        44 │ separable_con… │   N   │
│ (BatchNormalizat… │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_2      │ (None, 56, 56,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_4      │ (None, 56, 56,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_2… │ (None, 56, 56,  │       396 │ activation_2[… │   N 

 Total params: 4,290,856 (16.37 MB)

 Trainable params: 21,140 (82.58 KB)

 Non-trainable params: 4,269,716 (16.29 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 39s 323ms/step
Test accuracy on selected 20 classes: 2.80%


### 10. NASNetLarge

In [ ]:
from tensorflow.keras.applications import NASNetLarge
from tensorflow.keras.applications.nasnet import preprocess_input
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense
from sklearn.metrics import accuracy_score
import numpy as np
import random

#======================= Load the CIFAR-100 dataset =========================================#
(trainX, trainY), (testX, testY) = tf.keras.datasets.cifar100.load_data(label_mode='fine')
trainY = trainY.flatten()
testY = testY.flatten()

#======================= Randomly select 20 classes out of 100 ==============================#
selected_classes = random.sample(range(100), 20)
class_map = {original: new for new, original in enumerate(selected_classes)}

test_mask = np.isin(testY, selected_classes)
testX, testY = testX[test_mask], testY[test_mask]
testY = np.vectorize(class_map.get)(testY)

#======================= Resize and preprocess test images ==================================#
testX_resized = tf.image.resize(testX, (331, 331)).numpy()
testX_preprocessed = preprocess_input(testX_resized)

#======================= Load NASNetLarge pretrained model ==================================#
base_model = NASNetLarge(include_top=False, weights='imagenet', input_shape=(331, 331, 3))
base_model.trainable = False

x = base_model.output
x = GlobalAveragePooling2D()(x)
output = Dense(20, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=output, name="NASNetLarge-model")
model.summary(show_trainable=True)

#======================= Predict on test data ==============================================#
y_pred_probs = model.predict(testX_preprocessed)
predY = np.argmax(y_pred_probs, axis=1)

#======================= Evaluate accuracy ==================================================#
acc = accuracy_score(testY, predY) * 100
print(f"Test accuracy on selected 20 classes: {acc:.2f}%")


343610240/343610240 ━━━━━━━━━━━━━━━━━━━━ 9s 0us/step


Model: "NASNetLarge-model"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_6     │ (None, 331,     │         0 │ -              │   -   │
│ (InputLayer)      │ 331, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv1        │ (None, 165,     │     2,592 │ input_layer_6… │   N   │
│ (Conv2D)          │ 165, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn1          │ (None, 165,     │       384 │ stem_conv1[0]… │   N   │
│ (BatchNormalizat… │ 165, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_188    │ (None, 165,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 165, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_conv_1… │ (None, 165,     │     4,032 │ activation_18… │   N   │
│ (Conv2D)          │ 165, 42)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_bn_1_s… │ (None, 165,     │       168 │ reduction_con… │   N   │
│ (BatchNormalizat… │ 165, 42)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_189    │ (None, 165,     │         0 │ reduction_bn_… │   -   │
│ (Activation)      │ 165, 42)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_191    │ (None, 165,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 165, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 169,     │         0 │ activation_18… │   -   │
│ (ZeroPadding2D)   │ 169, 42)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 171,     │         0 │ activation_19… │   -   │
│ (ZeroPadding2D)   │ 171, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 83, 83,  │     2,814 │ separable_con… │   N   │
│ (SeparableConv2D) │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 83, 83,  │     8,736 │ separable_con… │   N   │
│ (SeparableConv2D) │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 83, 83,  │       168 │ separable_con… │   N   │
│ (BatchNormalizat… │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 83, 83,  │       168 │ separable_con… │   N   │
│ (BatchNormalizat… │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_190    │ (None, 83, 83,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_192    │ (None, 83, 83,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 42)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_2… │ (None, 83, 83,  │     2,814 │ activation_19… │   N 

 Total params: 84,997,478 (324.24 MB)

 Trainable params: 80,660 (315.08 KB)

 Non-trainable params: 84,916,818 (323.93 MB)

63/63 ━━━━━━━━━━━━━━━━━━━━ 113s 1s/step
Test accuracy on selected 20 classes: 3.40%
